# Split since the previous notebook was getting too large

# Setup

In [7]:
# Import all the necessary modules.
from dataclasses import dataclass
from enum import Enum
from IPython.core.display import HTML
import chess
import chess.pgn
import lucene
import os
import pandas as pd

# from org.apache.lucene.analysis.standard import StandardAnalyzer
from java.nio.file import Paths
from org.apache.lucene.analysis.core import WhitespaceAnalyzer
from org.apache.lucene.index import DirectoryReader
from org.apache.lucene.queryparser.classic import QueryParser
from org.apache.lucene.search import IndexSearcher
from org.apache.lucene.search.similarities import BM25Similarity
from org.apache.lucene.store import NIOFSDirectory

In [8]:
# Set up the Java VM for Lucene.

try:
    print("Initializing VM")
    lucene.initVM(vmargs=['-Djava.awt.headless=true'])  # This needs to be run once to get it all going
except ValueError as e:
    print("VM already initialized")

Initializing VM
VM already initialized


In [9]:
# Logic to convert between the chess board and our representation.

val_map = {i: str(1 - (7 * i / 64)) for i in range(1, 9)}
def r_closure(board):
    t = board.turn
    board.turn = chess.WHITE
    w_none_capture_moves = [move for move in board.legal_moves if not board.is_capture(move)]
    w_r_closure = [board.piece_at(x.from_square).symbol() + chess.square_name(x.to_square) + '^' + val_map[chess.square_distance(x.from_square, x.to_square)] for x in w_none_capture_moves]

    board.turn = chess.BLACK
    b_none_capture_moves = [move for move in board.legal_moves if not board.is_capture(move)]
    b_r_closure = [board.piece_at(x.from_square).symbol() + chess.square_name(x.to_square) + '^' + val_map[chess.square_distance(x.from_square, x.to_square)] for x in b_none_capture_moves]

    board.turn = t
    return w_r_closure + b_r_closure

def a_closure(board):
    t = board.turn
    
    board.turn = chess.WHITE
    w_capture_moves = [move for move in board.legal_moves if board.is_capture(move) and not board.is_en_passant(move)]
    w_a_closure = [board.piece_at(x.from_square).symbol() + ">" + board.piece_at(x.to_square).symbol() + chess.square_name(x.to_square) for x in w_capture_moves]

    board.turn = chess.BLACK
    b_capture_moves = [move for move in board.legal_moves if board.is_capture(move) and not board.is_en_passant(move)]
    b_a_closure = [board.piece_at(x.from_square).symbol() + ">" + board.piece_at(x.to_square).symbol() + chess.square_name(x.to_square) for x in b_capture_moves]

    board.turn = t
    return w_a_closure + b_a_closure

def d_closure(board):
    d_closure = []

    for square, piece in board.piece_map().items():
        if piece.piece_type != chess.KING: # Defending a king doesn't really make sense
            d_closure += [board.piece_at(x).symbol() + '<' + piece.symbol() + chess.square_name(square) for x in board.attackers(piece.color, square)]

    return d_closure

def p_closure(board):
    return [p.symbol()+chess.square_name(s) for s,p in board.piece_map().items()]

def encode_board_position(board):
    return  " ".join(r_closure(board)) + " " + " ".join(p_closure(board)) +" "+ " ".join(a_closure(board)) +" "+ " ".join(d_closure(board))

def decode_piece_position(pos):
    board = chess.Board()
    board.set_piece_map({chess.parse_square(term[1:]): chess.Piece.from_symbol(term[0]) for term in pos.strip().split(" ")})
    return board


In [11]:
# Load the puzzles to evaluate on from the CSV file.

df = pd.read_csv('../csvs/sub1600_games.csv')
print(df.shape)

def get_puzzle_board(index):
    fen = df.iloc[index]['FEN']
    board = chess.Board(fen)
    board.push(chess.Move.from_uci(df.iloc[index]['Moves'].split(" ")[0]))
    return board

def get_puzzle_solution(index):
    return df.iloc[index]['Moves'].split(" ")[1] # Only the first move

(214, 10)


In [12]:
# Define the query.

PATH = "../games/"

def run_query(searcher, analyzer, command, bound=10):
    """ Runs the actuall lucene query and collects the output. """
    escaped_command = command.replace("/", "\\/")
    query = QueryParser("contents", analyzer).parse(escaped_command)
    scoreDocs = searcher.search(query, bound).scoreDocs
    
    seen_games = set()
    output = []
    for scoreDoc in scoreDocs:
        doc = searcher.doc(scoreDoc.doc)
        link = f"https://lichess.org/{doc.get('game').split('.')[0]}#{int(doc.get('move'))}"
        
        # Skip any double matches for the games.
        if doc.get("game") in seen_games:
            continue
        
        file = open(os.path.join(PATH, doc.get("game")))
        file_content = str(file.read())
        content = file_content.split("\n")[int(doc.get("move"))-10].split("|")[0]
        header = file_content.split("\n")[0]
        file.close()
        
        output.append([doc.get('game'), doc.get('move'), link, scoreDoc.score, content, header])
        seen_games.add(doc.get("game"))
    
    return output

def score_lookup(board, bound):
    """ Wrapper for the lucene query to make it all function. """
    # output = []
    # directory = NIOFSDirectory(Paths.get("/Users/tobiaswilfert/Documents/University/IR/chess-db/games.index"))
    # searcher = IndexSearcher(DirectoryReader.open(directory))
    # searcher.setSimilarity(BM25Similarity())
    # analyzer = WhitespaceAnalyzer()
    # output = run_query(searcher, analyzer, command=encode_board_position(board), bound=bound)
    # del searcher  
    # return output 
    return run_query(searcher, analyzer, command=encode_board_position(board), bound=bound)


In [14]:
# The experiment logic.

class Outcome(Enum):
    WHITE_WON = 1
    BLACK_WON = -1
    DRAW = 0


# turn = 1 white and 0 black
def evaluate_move(turn, move, board, bound, top=5):
    output = score_lookup(board, bound)
    if len(output) < 5:
        raise ValueError(f"Not enough results found for {board} with bound={bound}.")
    
    # Sort the output by score and get the top_k
    output.sort(key=lambda x: x[3], reverse=True)
    top_k = output[:top]
    
    filtered_top_k = []
    for result in top_k:
        outcome = Outcome.WHITE_WON if "1-0" in result[5] else Outcome.BLACK_WON if "0-1" in result[5] else Outcome.DRAW
        filtered_top_k.append([result[3], outcome ,result[2], result[4]])
    
    # Calculate the score (unfiltered for now)
    if turn == 1:
        white_wins = sum([1 for x in filtered_top_k if x[1] == Outcome.WHITE_WON])
        score = white_wins / len(filtered_top_k)
    else:
        black_wins = sum([1 for x in filtered_top_k if x[1] == Outcome.BLACK_WON])
        score = black_wins / len(filtered_top_k)
    
    return [score, move, filtered_top_k]


def evaluate_position(turn, board, print_progress=False, bound=50, top=5):
    output = []
    
    for move in board.legal_moves:
        if print_progress: print(f"{move}, ", end="")
        board.push(move)
        output.append(evaluate_move(turn, move, board, bound, top))
        board.pop()
    
    return output
    

# Experiment

In [7]:
pred_correct = []
pred_wrong = []
res = []

directory = NIOFSDirectory(Paths.get("/Users/tobiaswilfert/Documents/University/IR/chess-db/games.index"))
searcher = IndexSearcher(DirectoryReader.open(directory))
searcher.setSimilarity(BM25Similarity())
analyzer = WhitespaceAnalyzer()

try:
    for i in range(0,100):
        puzzle = get_puzzle_board(i)
        solution = chess.Move.from_uci(get_puzzle_solution(i))
        display(HTML(chess.svg.board(board=puzzle, lastmove=solution, size=200)))
        temp = evaluate_position(puzzle.turn, puzzle, False, top=5, bound=40)
        print(f"#Moves: {puzzle.legal_moves.count()}, #Winning: {len([x for x in temp if x[0] > 0.5])}, #Losing: {len([x for x in temp if x[0] <= 0.5])}")
        solution_score = [x for x in temp if x[1] == solution][0]
        print(solution_score)
        if solution_score[0] > 0.5:
            pred_correct.append((i,solution_score))
            res.append(1)
        else:
            pred_wrong.append((i,solution_score))
            res.append(0)
except:
    del searcher

#Moves: 33, #Winning: 11, #Losing: 22
[0.4, Move.from_uci('f6e4'), [[27.7602596282959, <Outcome.BLACK_WON: -1>, 'https://lichess.org/rzhHnipM#16', 'rh8 ke8 bc8 ra8 ph7 pg7 pf7 qe7 pc7 pb7 bd6 pc6 pa6 ne4 Pd4 Nf3 Nc3 Ph2 Pg2 Pf2 Pc2 Pb2 Pa2 Rh1 Ke1 Qd1 Bc1 Ra1 '], [27.619691848754883, <Outcome.BLACK_WON: -1>, 'https://lichess.org/RQmn2HYT#44', 'rd8 ph7 Rg7 pf7 ke7 pc7 pb7 pf6 pe6 pa6 be5 Ph4 Pf3 Be3 Pc3 Pf2 Ke2 Pb2 Pa2 '], [27.54792594909668, <Outcome.WHITE_WON: 1>, 'https://lichess.org/RqBAyMol#38', 'rh8 ke8 rd8 ph7 bg7 pf7 pg6 pa6 pb5 Bf4 ne4 pc4 Ph3 Nc3 Pg2 Pf2 Pc2 Pb2 Pa2 Rh1 Ke1 Ra1 '], [27.506332397460938, <Outcome.WHITE_WON: 1>, 'https://lichess.org/IK6kHoYP#32', 'ke8 qd8 ra8 ph7 pf7 pc7 pb7 pa7 bd6 Qa5 ne4 nd4 pc4 Pf3 Pd3 Nc3 Ph2 rg2 Pc2 Pb2 Pa2 Rh1 Ke1 Bc1 Ra1 '], [27.376846313476562, <Outcome.WHITE_WON: 1>, 'https://lichess.org/JAew4ZIj#32', 'rh8 rd8 ph7 pg7 kd7 pc7 pb7 nf6 bd6 pc6 pa6 Pd3 Nc3 Ph2 Pg2 Pf2 Pc2 Pb2 Pa2 Kf1 Re1 Bc1 Ra1 ']]]


#Moves: 36, #Winning: 22, #Losing: 14
[0.6, Move.from_uci('c8e6'), [[35.911354064941406, <Outcome.WHITE_WON: 1>, 'https://lichess.org/PVW69UZM#64', 'kh8 rf8 rc8 pe7 pa7 Qg6 bf6 Pe6 pb6 ph5 Nf5 pc5 Ph4 Pc4 qa4 Pg3 Pd3 Pa3 Pf2 Re2 Kg1 Rb1 '], [33.39900207519531, <Outcome.BLACK_WON: -1>, 'https://lichess.org/AL5B837Q#20', 'rh8 ke8 qd8 nb8 ra8 pf7 pe7 pb7 pa7 ph6 pg6 bf6 pd6 pc5 Ph4 Qf4 Pe4 bc4 Pd3 Pc3 Pg2 Pf2 Nd2 Pb2 Pa2 Rh1 Ng1 Ke1 Ra1 '], [32.519229888916016, <Outcome.BLACK_WON: -1>, 'https://lichess.org/7csGEdhJ#16', 'rh8 ke8 qd8 ra8 ph7 pf7 pe7 pb7 pa7 pg6 bf6 be6 pd6 nc6 pc5 Ph4 Pe4 Qf3 Pd3 Pc3 Pg2 Pf2 Pb2 Pa2 Rh1 Ng1 Bf1 Ke1 Nb1 Ra1 '], [32.407039642333984, <Outcome.BLACK_WON: -1>, 'https://lichess.org/wtnPNrsA#47', 'kh8 ra8 pg7 Qf7 ph6 bf6 bc6 pa6 nd5 pb5 qa5 Ph4 pc4 Pg3 Pc3 Pf2 Bc2 Pb2 Pa2 Rh1 Rd1 Kc1 '], [32.31769561767578, <Outcome.WHITE_WON: 1>, 'https://lichess.org/fBYq12cP#52', 'rh8 kd8 rc8 Qf7 pe7 pg6 bf6 be6 pd6 pa6 pb5 Ph3 Nf3 Pg2 qc2 Pb2 Pa2 Kh1 Rf1 Bc1 Ra1 ']]]


#Moves: 6, #Winning: 5, #Losing: 1
[0.6, Move.from_uci('d2e3'), [[36.145816802978516, <Outcome.WHITE_WON: 1>, 'https://lichess.org/bNnZgrq0#37', 'kg8 rf8 ra8 Bg7 pf7 be7 bb7 pe6 nc6 pa6 Qh5 Pe5 qa5 Ph4 Be4 pc4 pc3 Pg2 Pf2 Pc2 Pb2 Pa2 Rh1 Rd1 Kb1 '], [35.460693359375, <Outcome.BLACK_WON: -1>, 'https://lichess.org/SdqaTnzr#44', 'rh8 kg8 rc8 bg7 Qe7 nd7 pg6 nf6 pd6 pa6 pg5 bd5 qa5 Ph4 Pd4 pb4 Pf3 Bd3 pc3 Bf2 Pc2 Pb2 Pa2 Rh1 Re1 Kb1 '], [34.53725814819336, <Outcome.WHITE_WON: 1>, 'https://lichess.org/oJtEf46W#45', 'kg8 rf8 ra8 ph7 qe7 Qh6 pe6 pc6 pg5 pf5 Pe5 Pc5 Ph4 pe4 Pd4 pb4 Na4 Pg3 Pe3 bd3 Pb3 Kd2 Rh1 Ra1 '], [34.08127975463867, <Outcome.BLACK_WON: -1>, 'https://lichess.org/lhfLza9T#59', 'kg8 rf8 ra8 ph7 pa7 Qh6 pg6 pe6 pc6 ba6 qf5 Pe5 Ph4 pb4 pc3 Pf2 Pb2 Pa2 Kh1 Rg1 '], [33.80784606933594, <Outcome.WHITE_WON: 1>, 'https://lichess.org/LfLl1tCi#33', 'kg8 rf8 be8 rc8 qe7 pc7 pb7 pa7 Qh6 pe6 nc6 pg5 pf5 Pe5 pd5 Ph4 Pd4 Bg3 Pe3 Pc3 Pg2 Nd2 Pb2 Pa2 Rh1 Ke1 Ra1 ']]]


#Moves: 34, #Winning: 12, #Losing: 22
[0.4, Move.from_uci('c5a7'), [[27.099559783935547, <Outcome.WHITE_WON: 1>, 'https://lichess.org/P1Hl0N45#90', 'pa7 ph6 ke6 Bh5 rd5 Kh3 Pg3 qe3 Ph2 pd2 Pa2 Rf1 Rd1 '], [25.462324142456055, <Outcome.BLACK_WON: -1>, 'https://lichess.org/j8BpgVaD#75', 'kf8 re8 pf7 Pf5 pe5 pb5 Kh4 Rg4 Pe4 Pg3 Ph2 qe2 pd2 '], [24.235750198364258, <Outcome.BLACK_WON: -1>, 'https://lichess.org/AJJjeNvX#113', 'rh8 rh7 Qa7 ke6 pf5 qd5 pb5 pg4 Pg3 pc3 Ph2 Re2 pd2 Kg1 '], [24.13669776916504, <Outcome.BLACK_WON: -1>, 'https://lichess.org/XWTAvEcd#65', 'pf7 ke7 Qb7 ph6 pe6 Pf5 pa5 re4 Pa4 rd3 Ph2 Ne2 pd2 qc2 Kh1 Rf1 Rd1 '], [24.0648193359375, <Outcome.WHITE_WON: 1>, 'https://lichess.org/TXqQEtUu#75', 'kf8 Qa8 pg7 re7 ph6 pf6 pa5 qd4 Pg3 Ph2 Kg2 Pf2 pd2 Pb2 Pa2 Rd1 ']]]


#Moves: 40, #Winning: 21, #Losing: 19
[0.6, Move.from_uci('d3e2'), [[39.50059127807617, <Outcome.BLACK_WON: -1>, 'https://lichess.org/SJ82Bup4#53', 'kh8 rf8 rc8 ph7 pb7 pg6 ne6 nc6 pa6 Ph4 qg4 pd4 Pg3 Pf2 Be2 Pc2 Pb2 Pa2 Kg1 Qf1 Rd1 '], [39.3752326965332, <Outcome.BLACK_WON: -1>, 'https://lichess.org/ZLqSuKYa#39', 'kg8 rf8 re8 pg7 nd7 bb7 pa7 ph6 pf6 pe6 pb6 Pe5 pd5 Ph4 qg4 Nf4 Pd4 Pg3 Pa3 Kh2 Pf2 Be2 Qd2 Pb2 Rf1 Ra1 '], [39.25244903564453, <Outcome.WHITE_WON: 1>, 'https://lichess.org/sL3rpVJI#53', 'kg8 rf8 bc8 nb8 ra8 pg7 pf7 be7 pd7 pa7 ph6 pc6 Pf5 Pe5 pb5 Ph4 qg4 Nf4 Nd4 Pg3 Kh2 Be2 Qd2 Bb2 Pa2 Rf1 '], [38.217376708984375, <Outcome.WHITE_WON: 1>, 'https://lichess.org/Ew4nAxps#45', 'kg8 rf8 re8 ph7 pf7 nd7 pg6 pd6 pb6 qf5 pc5 pa5 Ph4 Nf4 bd4 Pa4 Pg3 Pf3 Pb3 Qd2 Pc2 Rh1 Kf1 Rb1 '], [37.77707290649414, <Outcome.WHITE_WON: 1>, 'https://lichess.org/WjA0W3Eg#49', 'kg8 rf8 rb8 ph7 pf7 bb7 pg6 pe6 pa6 qg4 pd4 Pb3 Ph2 Pg2 Qf2 Be2 Pa2 Kg1 Re1 Rc1 ']]]


...

#Moves: 9, #Winning: 0, #Losing: 9
[0.4, Move.from_uci('g6c2'), [[38.8425407409668, <Outcome.BLACK_WON: -1>, 'https://lichess.org/Rv1N0j5I#64', 'rf8 rc8 kd7 pe6 bc6 pg5 Pe5 pd5 Pc5 pa5 ph4 Pg4 Nd4 Rc3 Pa3 Ph2 Ba2 Kg1 Rc1 '], [36.06047821044922, <Outcome.BLACK_WON: -1>, 'https://lichess.org/4Lt6VOgO#55', 'kg8 rd8 rc8 ph7 pf7 be7 qb7 pg6 bc6 Pe5 pd5 pa5 Pf4 Nd4 pb4 Pa4 Pg3 Qe3 pc3 Pb3 Ph2 Pc2 Ba2 Kg1 Rd1 Ra1 '], [34.8577766418457, <Outcome.WHITE_WON: 1>, 'https://lichess.org/FQuJ5KYo#49', 'kg8 rf8 rc8 ph7 pg7 pf7 pb7 pe6 bc6 Pe5 nd5 pa5 Pf4 Nd4 Rc4 Pa4 Pg3 Pb3 qa3 Ph2 Bg2 Qe2 Kh1 Rb1 '], [34.66264343261719, <Outcome.WHITE_WON: 1>, 'https://lichess.org/BDN1nKeJ#66', 'Rg8 rd8 rc8 pf7 kd7 pb7 Qf6 pe6 bc6 pa6 ph5 Pe5 pd5 qc5 Pf4 Bd3 Ph2 Pc2 Pb2 Kh1 Ra1 '], [34.56572341918945, <Outcome.BLACK_WON: -1>, 'https://lichess.org/BakoCUnx#67', 'rg8 rc8 pf7 qe7 kd7 pb7 pe6 bc6 pa6 Re5 pd5 Pc5 Ph4 Pd4 Pa4 Bd3 Pg2 Pf2 Qd2 Kg1 Ra1 ']]]


#Moves: 56, #Winning: 18, #Losing: 38
[0.4, Move.from_uci('f4h3'), [[49.31907272338867, <Outcome.BLACK_WON: -1>, 'https://lichess.org/Gk5Bq9Dh#20', 'kg8 rf8 qd8 ra8 ph7 pg7 pf7 pc7 pb7 pa7 pe6 nc6 bf5 bc5 Bc4 nh3 Pg3 Nf3 Pd3 Pa3 Pf2 Pc2 Pb2 Kg1 Rf1 Qd1 Nb1 Ra1 '], [47.686424255371094, <Outcome.WHITE_WON: 1>, 'https://lichess.org/wMzVLGHD#18', 'kg8 rf8 qd8 ra8 ph7 pg7 pf7 be7 pc7 pb7 pa7 be6 nc6 pe5 nf4 Ph3 Nf3 Pd3 Pa3 Pg2 Pf2 Pc2 Pb2 Ba2 Kg1 Rf1 Qd1 Bc1 Nb1 Ra1 '], [47.27510070800781, <Outcome.BLACK_WON: -1>, 'https://lichess.org/7Lj8LlXW#17', 'kg8 rf8 qd8 ra8 ph7 pg7 pf7 pc7 pb7 pa7 be6 nc6 pe5 nd5 bc5 Ph3 Pd3 Pa3 Pg2 Pf2 Ne2 Pc2 Pb2 Ba2 Kg1 Rf1 Qd1 Bc1 Nb1 Ra1 '], [47.176971435546875, <Outcome.WHITE_WON: 1>, 'https://lichess.org/Uk0GiejX#15', 'kg8 rf8 qd8 ra8 ph7 pg7 pf7 pc7 pb7 pa7 nf6 be6 pd6 nc6 pe5 bc5 Pe4 Ph3 Nf3 Pd3 Pa3 Pg2 Pf2 Pc2 Pb2 Ba2 Kg1 Rf1 Qd1 Bc1 Nb1 Ra1 '], [47.176971435546875, <Outcome.WHITE_WON: 1>, 'https://lichess.org/9CiG5ik6#15', 'kg8 rf8 qd8 ra8 ph7 pg7 pf7 pc7

#Moves: 44, #Winning: 30, #Losing: 14
[0.6, Move.from_uci('f4g6'), [[41.49680709838867, <Outcome.BLACK_WON: -1>, 'https://lichess.org/ZjAmBZQr#27', 'kh8 rf8 qd8 ra8 ph7 pg7 pf7 pb7 pa7 Ng6 nf6 bd6 nc6 pe5 pd4 Ph3 Ng3 Pd3 Bb3 Pg2 Pf2 Pc2 Pb2 Pa2 Kg1 Re1 Qd1 Bc1 Ra1 '], [39.593849182128906, <Outcome.WHITE_WON: 1>, 'https://lichess.org/1vL6Tfrk#36', 'kh8 rf8 qd8 ra8 ph7 pg7 bd7 pb7 pa7 nb6 pe5 pc5 Ph4 Pe4 pd4 Pc3 Bb3 Ph2 Pg2 Qe2 Nd2 Pb2 Pa2 Kg1 Rf1 Ra1 '], [38.58072280883789, <Outcome.BLACK_WON: -1>, 'https://lichess.org/ovW3d0Cj#37', 'kh8 rf8 qd8 ra8 ph7 pg7 bd7 pc7 pb7 pd6 nc6 bb6 pe5 pa5 Nh4 Pe4 Pd3 Pc3 Bb3 Qh2 Pg2 Pb2 Pa2 Kh1 Rf1 Bc1 Ra1 '], [36.703857421875, <Outcome.WHITE_WON: 1>, 'https://lichess.org/1xxCymzQ#22', 'kg8 rf8 qd8 ra8 ph7 pg7 pf7 pc7 pb7 pa7 nc6 nb6 pe5 Pd3 Pc3 Bb3 Ph2 Pg2 Pf2 Qe2 Bd2 Pc2 Pa2 Kg1 Rf1 Ra1 '], [35.76496124267578, <Outcome.WHITE_WON: 1>, 'https://lichess.org/U8yQql42#37', 'kg8 rf8 qd8 ra8 ph7 pg7 pf7 bd7 pb7 pa7 Ng6 pd6 pc6 nf5 Pd4 Ph3 Nc3 Bb3 Pg2 Qf2 Pc2

#Moves: 41, #Winning: 21, #Losing: 20
[0.6, Move.from_uci('e2h5'), [[43.61500549316406, <Outcome.WHITE_WON: 1>, 'https://lichess.org/0j9H8ugH#42', 'rh8 ke8 rc8 pg7 pf7 bd7 pb7 ph6 nf6 pe6 qc6 pa6 pd5 Pa5 Pb4 Nf3 Bd3 Pc3 Ph2 Pg2 Pf2 Qc2 Kg1 Rf1 Ra1 '], [42.49705505371094, <Outcome.BLACK_WON: -1>, 'https://lichess.org/kvQwFsJg#41', 'kg8 rc8 ph7 bg7 bd7 pg6 rf6 pe6 qc6 pa6 pd5 pb5 Bg4 Bf4 Pd4 Pb4 Ph3 Pc3 Pa3 Pg2 Qd2 Kg1 Rf1 Rc1 '], [41.02991485595703, <Outcome.WHITE_WON: 1>, 'https://lichess.org/CUQzNzYi#38', 'rh8 ke8 pg7 nf7 be7 bd7 pb7 Bg6 pe6 qb6 pa6 pf5 Pe5 pd5 Pd4 Pb4 Ph3 Nf3 Pa3 Pg2 Pf2 Qc2 Bb2 Kg1 Rf1 '], [39.58370590209961, <Outcome.BLACK_WON: -1>, 'https://lichess.org/HkFmNJII#39', 'rh8 ke8 rc8 nf7 bd7 pb7 Qg6 pe6 qb6 pa6 ph5 Pg5 Pe5 pd5 Nc3 Pg2 Pf2 Pb2 Pa2 Kg1 Rc1 Ra1 '], [39.220855712890625, <Outcome.WHITE_WON: 1>, 'https://lichess.org/sq3gMYwP#45', 'kg8 rf8 nd8 rc8 pg7 nf7 be7 pb7 pa7 ph6 qc6 Bh5 Rf5 Pd4 Pb4 Pc3 Qb3 Na3 Ph2 Pg2 Bd2 Kh1 Ra1 ']]]


#Moves: 37, #Winning: 7, #Losing: 30
[0.6, Move.from_uci('f7g8'), [[37.91560745239258, <Outcome.DRAW: 0>, 'https://lichess.org/qpRr1yYW#81', 'Qg8 Rb8 kh7 pg7 ph6 Pg3 Pe3 Ph2 Kg1 '], [33.842994689941406, <Outcome.BLACK_WON: -1>, 'https://lichess.org/Km6vI78Q#65', 'Qg8 Rb8 kh7 pg7 pa7 pe6 ph5 pd5 rh4 qg4 ne4 Pg3 Pf2 Pa2 Kg1 Rf1 '], [33.072208404541016, <Outcome.WHITE_WON: 1>, 'https://lichess.org/bHRVtFF1#55', 'Qg8 Rb8 kh7 pg7 ph6 pd6 pa6 qh4 Pe4 Pa4 bg3 Ph2 Kg1 Rf1 '], [32.415802001953125, <Outcome.WHITE_WON: 1>, 'https://lichess.org/wvQ66LFq#65', 'Qg8 Rc8 kh7 pg7 ph6 pe6 nd5 qg4 Pa4 Pg3 Nf3 Kh2 Pg2 Pf2 Pb2 rd1 '], [32.25389099121094, <Outcome.WHITE_WON: 1>, 'https://lichess.org/jOesd2bB#83', 'Qg8 Rb8 kh7 pg7 pa7 ph6 Pe5 Pc5 Pf4 be4 Pc4 Pa4 Ph3 Kh2 Pg2 qf2 ']]]


In [8]:
print(len(res))
print(len(pred_correct))
print(len(pred_wrong))

100
58
42


In [9]:
print(res)

[0, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 0, 0, 0, 0, 1, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 1, 1, 0, 1, 0, 0, 1, 1, 0, 1, 1, 0, 1, 0, 1, 1, 0, 1, 0, 0, 0, 1, 0, 1, 1, 0, 1, 1, 1, 1, 1, 0, 0, 0, 1, 1, 1, 0, 1, 0, 0, 0, 1, 0, 1, 1, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 1, 1, 0, 0, 1, 1, 1]


In [10]:
print(pred_correct)

[(1, [0.6, Move.from_uci('c8e6'), [[35.911354064941406, <Outcome.WHITE_WON: 1>, 'https://lichess.org/PVW69UZM#64', 'kh8 rf8 rc8 pe7 pa7 Qg6 bf6 Pe6 pb6 ph5 Nf5 pc5 Ph4 Pc4 qa4 Pg3 Pd3 Pa3 Pf2 Re2 Kg1 Rb1 '], [33.39900207519531, <Outcome.BLACK_WON: -1>, 'https://lichess.org/AL5B837Q#20', 'rh8 ke8 qd8 nb8 ra8 pf7 pe7 pb7 pa7 ph6 pg6 bf6 pd6 pc5 Ph4 Qf4 Pe4 bc4 Pd3 Pc3 Pg2 Pf2 Nd2 Pb2 Pa2 Rh1 Ng1 Ke1 Ra1 '], [32.519229888916016, <Outcome.BLACK_WON: -1>, 'https://lichess.org/7csGEdhJ#16', 'rh8 ke8 qd8 ra8 ph7 pf7 pe7 pb7 pa7 pg6 bf6 be6 pd6 nc6 pc5 Ph4 Pe4 Qf3 Pd3 Pc3 Pg2 Pf2 Pb2 Pa2 Rh1 Ng1 Bf1 Ke1 Nb1 Ra1 '], [32.407039642333984, <Outcome.BLACK_WON: -1>, 'https://lichess.org/wtnPNrsA#47', 'kh8 ra8 pg7 Qf7 ph6 bf6 bc6 pa6 nd5 pb5 qa5 Ph4 pc4 Pg3 Pc3 Pf2 Bc2 Pb2 Pa2 Rh1 Rd1 Kc1 '], [32.31769561767578, <Outcome.WHITE_WON: 1>, 'https://lichess.org/fBYq12cP#52', 'rh8 kd8 rc8 Qf7 pe7 pg6 bf6 be6 pd6 pa6 pb5 Ph3 Nf3 Pg2 qc2 Pb2 Pa2 Kh1 Rf1 Bc1 Ra1 ']]]), (2, [0.6, Move.from_uci('d2e3'), [[36.14

In [11]:
print(pred_wrong)

[(0, [0.4, Move.from_uci('f6e4'), [[27.7602596282959, <Outcome.BLACK_WON: -1>, 'https://lichess.org/rzhHnipM#16', 'rh8 ke8 bc8 ra8 ph7 pg7 pf7 qe7 pc7 pb7 bd6 pc6 pa6 ne4 Pd4 Nf3 Nc3 Ph2 Pg2 Pf2 Pc2 Pb2 Pa2 Rh1 Ke1 Qd1 Bc1 Ra1 '], [27.619691848754883, <Outcome.BLACK_WON: -1>, 'https://lichess.org/RQmn2HYT#44', 'rd8 ph7 Rg7 pf7 ke7 pc7 pb7 pf6 pe6 pa6 be5 Ph4 Pf3 Be3 Pc3 Pf2 Ke2 Pb2 Pa2 '], [27.54792594909668, <Outcome.WHITE_WON: 1>, 'https://lichess.org/RqBAyMol#38', 'rh8 ke8 rd8 ph7 bg7 pf7 pg6 pa6 pb5 Bf4 ne4 pc4 Ph3 Nc3 Pg2 Pf2 Pc2 Pb2 Pa2 Rh1 Ke1 Ra1 '], [27.506332397460938, <Outcome.WHITE_WON: 1>, 'https://lichess.org/IK6kHoYP#32', 'ke8 qd8 ra8 ph7 pf7 pc7 pb7 pa7 bd6 Qa5 ne4 nd4 pc4 Pf3 Pd3 Nc3 Ph2 rg2 Pc2 Pb2 Pa2 Rh1 Ke1 Bc1 Ra1 '], [27.376846313476562, <Outcome.WHITE_WON: 1>, 'https://lichess.org/JAew4ZIj#32', 'rh8 rd8 ph7 pg7 kd7 pc7 pb7 nf6 bd6 pc6 pa6 Pd3 Nc3 Ph2 Pg2 Pf2 Pc2 Pb2 Pa2 Kf1 Re1 Bc1 Ra1 ']]]), (3, [0.4, Move.from_uci('c5a7'), [[27.099559783935547, <Outcome.WHITE_

In [13]:
correct_similarity = [x[1][2][0][0] for x in pred_correct]
wrong_similarity = [x[1][2][0][0] for x in pred_wrong]
print(sum(correct_similarity)/len(correct_similarity))
print(sum(wrong_similarity)/len(wrong_similarity))

correct_similarity = [sum([y[0] for y in x[1][2]])/5 for x in pred_correct]
wrong_similarity = [sum([y[0] for y in x[1][2]])/5 for x in pred_wrong]
print(sum(correct_similarity)/len(correct_similarity))
print(sum(wrong_similarity)/len(wrong_similarity))

34.516711119947765
35.423412777128675
32.705104285273066
33.35163417543684


# More difficult games

In [18]:
sorted_df_output = pd.read_csv('sorted_df_output.csv')
sorted_df_output = sorted_df_output.iloc[100:]
sorted_df_output = sorted_df_output[sorted_df_output['Rating'] > 1600]
df = sorted_df_output.iloc[:100]

df.to_csv('16plus.csv', index=False)

df.shape

(100, 10)

In [19]:
directory = NIOFSDirectory(Paths.get("/Users/tobiaswilfert/Documents/University/IR/chess-db/games.index"))
searcher = IndexSearcher(DirectoryReader.open(directory))
searcher.setSimilarity(BM25Similarity())
analyzer = WhitespaceAnalyzer()

try:
    for i in range(0,100):
        puzzle = get_puzzle_board(i)
        solution = chess.Move.from_uci(get_puzzle_solution(i))
        display(HTML(chess.svg.board(board=puzzle, lastmove=solution, size=200)))
        temp = evaluate_position(puzzle.turn, puzzle, False, top=5, bound=50)
        print(f"#Moves: {puzzle.legal_moves.count()}, #Winning: {len([x for x in temp if x[0] > 0.5])}, #Losing: {len([x for x in temp if x[0] <= 0.5])}")
        solution_score = [x for x in temp if x[1] == solution][0]
        print(solution_score)
        if solution_score[0] > 0.5:
            pred_correct.append((i,solution_score))
            res.append(1)
        else:
            pred_wrong.append((i,solution_score))
            res.append(0)
except:
    del searcher

#Moves: 51, #Winning: 6, #Losing: 45
[0.2, Move.from_uci('a6e2'), [[40.6551399230957, <Outcome.BLACK_WON: -1>, 'https://lichess.org/24LU32SS#41', 'kg8 rf8 re8 pg7 pf7 be7 Bc7 pa7 ph6 nf6 Bf5 pd5 pb5 Pd4 qb4 Pe3 Qc3 Ph2 Pg2 Pf2 Pb2 Pa2 Kg1 Rc1 Ra1 '], [39.956016540527344, <Outcome.WHITE_WON: 1>, 'https://lichess.org/JIQXNevK#57', 'kg8 bf8 pf7 ph6 pb6 pg5 pd5 pa5 Pd4 qb4 Ph3 Pe3 Qc3 Pb3 Pg2 Pf2 Rc2 Pa2 Kg1 Rf1 '], [38.76308822631836, <Outcome.WHITE_WON: 1>, 'https://lichess.org/eG2suWMz#48', 'kg8 bf8 re8 qa8 pg7 pf7 nd7 bb7 ph6 nf6 Nc6 pb6 pa6 Bf5 pd5 Nd4 Pb4 Ph3 Bg3 Pe3 Qd3 Pa3 Pg2 Pf2 Kg1 Rc1 '], [37.85543441772461, <Outcome.WHITE_WON: 1>, 'https://lichess.org/ZXimz7wa#49', 'kg8 bf8 re8 qd8 pg7 pf7 nd7 ph6 nf6 Qc6 pb6 Bf5 pd5 pa5 Ph3 Bg3 Pe3 Pa3 Pg2 Pf2 Pb2 Kg1 Rd1 Rc1 '], [37.18400955200195, <Outcome.WHITE_WON: 1>, 'https://lichess.org/XiHavdAr#30', 'rh8 bf8 rd8 kc8 pg7 pf7 pc7 pb7 ph6 nf6 pe6 pa6 bh5 ne4 Pd4 qb4 Na4 Ph3 Bg3 Nf3 Qc3 Pb3 Pg2 Pf2 Be2 Pc2 Pa2 Kg1 Rf1 Ra1 ']]]


#Moves: 36, #Winning: 14, #Losing: 22
[0.4, Move.from_uci('g5f4'), [[35.28987503051758, <Outcome.BLACK_WON: -1>, 'https://lichess.org/rOW80bV7#64', 'kf8 rd8 pf7 pa7 ph6 pg6 pc6 bd5 qf4 Pb3 Ph2 Pg2 Pf2 Pc2 Pa2 Re1 Kb1 '], [30.849550247192383, <Outcome.WHITE_WON: 1>, 'https://lichess.org/IJI1gUna#84', 're8 kh7 pf7 pg6 Qa6 ph5 Be5 Rb5 qe3 Pd3 Pb3 Pc2 Kb2 '], [30.688922882080078, <Outcome.WHITE_WON: 1>, 'https://lichess.org/cBheo4go#55', 'kf8 Bb8 pg7 pb7 pa7 ph6 pc6 pg5 bd5 Pc3 Pb3 Pa3 Ph2 Pg2 Pc2 Kb1 '], [30.382057189941406, <Outcome.BLACK_WON: -1>, 'https://lichess.org/IHSI4vm7#66', 'kh7 rf7 pb7 pa7 ph6 Pf6 Qd6 pc6 pg5 pe5 Rg4 be4 qf3 Pb3 Pc2 Pa2 Rg1 Kb1 '], [30.164623260498047, <Outcome.WHITE_WON: 1>, 'https://lichess.org/FdiCwNZS#81', 'ka8 ph7 Re7 pg6 Nf6 pb6 pa6 pf5 Be5 qf4 Ph3 Pd3 Pb3 Pc2 Kb2 ']]]


#Moves: 42, #Winning: 34, #Losing: 8
[0.8, Move.from_uci('g4h2'), [[41.681617736816406, <Outcome.BLACK_WON: -1>, 'https://lichess.org/ijGoMdc9#37', 'kg8 rf8 bc8 rb8 pf7 qc7 pb7 pa7 pg6 pe6 ph5 Ph4 ng4 Pf4 bd4 Bc4 Ng3 Qf3 Pd3 Pa3 Pg2 Pb2 Kh1 Rf1 Bc1 Rb1 '], [40.80215835571289, <Outcome.BLACK_WON: -1>, 'https://lichess.org/hwbAleum#31', 'kg8 rf8 qd8 ra8 ph7 pg7 pf7 nd7 pb7 ba7 bf5 Ne5 pd5 pa5 Pf4 pd4 Ph3 Qf3 Pd3 Pa3 Pg2 Pc2 Pb2 Ba2 Kg1 Rf1 Bc1 Ra1 '], [38.62944793701172, <Outcome.BLACK_WON: -1>, 'https://lichess.org/UaZNW8MK#26', 'kg8 rf8 qd8 ra8 ph7 pg7 pf7 pb7 pa7 pe6 bf5 ne5 Bb5 Qf3 Pe3 Pd3 Nc3 Ph2 Pg2 Pc2 Pb2 Pa2 Rh1 Ke1 Ra1 '], [38.61678695678711, <Outcome.WHITE_WON: 1>, 'https://lichess.org/pOuM4WQX#34', 'kh8 rf8 qd8 ra8 pg7 pf7 ne7 pc7 pb7 ph6 pb6 bf5 Pe5 Pf4 Bc4 Qf3 Pd3 Pa3 Ph2 Pc2 Pb2 Kh1 Rg1 Bc1 Ra1 '], [38.50428771972656, <Outcome.BLACK_WON: -1>, 'https://lichess.org/78V0vgOw#26', 'kg8 rf8 qd8 rb8 ph7 pg7 pf7 be7 nd7 pe6 Bc6 pa6 bf5 pc5 pb5 Pf4 Qf3 Pd3 Ph2 Pg2 Pc2 Pb2 Pa2 Kg1 

#Moves: 39, #Winning: 38, #Losing: 1
[0.6, Move.from_uci('c5f8'), [[41.49925231933594, <Outcome.BLACK_WON: -1>, 'https://lichess.org/E8g4na2T#39', 'kg8 Qf8 ra8 ph7 bg7 pb7 pa7 pg6 pc6 Bg5 pd5 be4 Ph2 Pg2 Pf2 Pb2 Pa2 Kg1 Re1 Ra1 '], [39.76523208618164, <Outcome.WHITE_WON: 1>, 'https://lichess.org/AK9daUef#41', 'kg8 rf8 ph7 pg7 pb7 pa7 pg6 bd6 pc6 nh5 qg5 pd5 Pf4 Pd4 Pg3 Pe3 Pc3 Ph2 Bg2 Qd2 Pb2 Pa2 Kg1 Rf1 Re1 '], [38.16410827636719, <Outcome.WHITE_WON: 1>, 'https://lichess.org/9mTfT26V#39', 'kg8 Qf8 rc8 ph7 bg7 pa7 pg6 pe6 nc6 pb6 ba6 Pe5 pd5 pc5 Pd4 Ph3 Pg3 Pc3 Pa3 Kh2 Bg2 Ne2 Bd2 Pb2 Ra1 '], [36.906959533691406, <Outcome.BLACK_WON: -1>, 'https://lichess.org/6NLqKUis#39', 'kg8 Qf8 ra8 nh7 ne7 bd7 pb7 ph6 pg6 pc6 pd5 pa5 Nh4 bd4 Pa4 Nc3 Ph2 Pg2 Pc2 Pb2 Ba2 Kh1 Bc1 Ra1 '], [36.65887451171875, <Outcome.WHITE_WON: 1>, 'https://lichess.org/WWd0vBE7#47', 'kg8 Qf8 rb8 bg7 pf7 qc7 ph6 pg6 ne6 pb6 pa5 Bh4 Ne4 Qf3 Ph2 Pg2 Pb2 Pa2 Kg1 Rf1 Rd1 ']]]


#Moves: 42, #Winning: 1, #Losing: 41
[0.6, Move.from_uci('e6g4'), [[40.33609390258789, <Outcome.BLACK_WON: -1>, 'https://lichess.org/9tJjQPr5#32', 'rh8 rd8 kb8 pg7 pf7 ne7 pc7 pb7 ph6 qg6 pc6 pa6 bg4 Pe4 Pc4 Pb4 Qf3 Pd3 Nc3 Ph2 Pg2 Pf2 Pa2 Kg1 Rf1 Ne1 Ra1 '], [38.99119186401367, <Outcome.BLACK_WON: -1>, 'https://lichess.org/39MdVqHS#52', 'rh8 rd8 kb8 pf7 pb7 pa7 ph6 pe6 Pc6 bc5 qh4 bg4 Bc4 Qf3 Re3 Pd3 Nc3 Pa3 Pg2 Ke2 Pc2 Rd1 '], [37.645816802978516, <Outcome.BLACK_WON: -1>, 'https://lichess.org/DYkYfdsm#29', 'rh8 rd8 kc8 pg7 pf7 pc7 pb7 pa7 pc6 ph5 qg5 Pe4 Qf3 Ne3 Pd3 Ph2 Pg2 Ke2 bd2 Pc2 Pb2 Pa2 Rh1 Ra1 '], [36.12165451049805, <Outcome.WHITE_WON: 1>, 'https://lichess.org/aXqov6Vx#54', 'rh8 rd8 kc8 bd7 ph6 pf6 pc6 Pf5 pe5 Qb4 Ra3 Ph2 Pg2 qf2 Kd2 Pb2 Ne1 Rd1 '], [35.73238754272461, <Outcome.WHITE_WON: 1>, 'https://lichess.org/ek5X43dD#47', 'rd8 kb8 bc7 pb7 pa7 pf6 ph5 re5 Ph3 Qf3 Ne3 qh2 Pg2 Pf2 Ke2 Pc2 Pb2 Pa2 Rd1 Ra1 ']]]


...

#Moves: 34, #Winning: 32, #Losing: 2
[0.8, Move.from_uci('e6d7'), [[27.102657318115234, <Outcome.WHITE_WON: 1>, 'https://lichess.org/zqfetvf2#39', 'rh8 ke8 ra8 pf7 Bd7 ph6 pa6 pg5 qe5 pd5 pc5 pb5 Qb4 Ph3 Pe3 Pc3 Pa3 Pg2 Pf2 Pb2 Rh1 Ke1 Ra1 '], [27.092193603515625, <Outcome.BLACK_WON: -1>, 'https://lichess.org/FiXN3Crz#31', 'rh8 ke8 nb8 ra8 pf7 pc7 pb7 pa7 ph6 Bc6 pg5 qe5 pd5 Pe3 Pc3 Qb3 Ph2 Pg2 Pf2 Pb2 Pa2 Rh1 Ke1 Nb1 Ra1 '], [26.577213287353516, <Outcome.WHITE_WON: 1>, 'https://lichess.org/QAviSzNG#31', 'rh8 ke8 ra8 Bf7 qe7 pc7 pb7 pa7 ph6 nc6 nh5 pg5 bc5 pf4 Pf3 Pc3 Qb3 Ph2 Pb2 Pa2 Kh1 Re1 Bc1 Nb1 Ra1 '], [26.52043342590332, <Outcome.WHITE_WON: 1>, 'https://lichess.org/0U7XRnNe#45', 'rh8 kd8 ra8 Bd7 pb7 pa7 ph6 pc6 bg5 pe5 Pe3 Pc3 Qb3 Nh2 Pg2 Pb2 Pa2 Kg1 Rf1 '], [26.245615005493164, <Outcome.WHITE_WON: 1>, 'https://lichess.org/hbzLYEPf#21', 'rh8 bf8 ke8 qd8 ra8 pg7 pf7 Bd7 pc7 pb7 pa7 ph6 nf6 nb6 Pd5 pf4 Nf3 Pd3 Pc3 Qb3 Ph2 Pg2 Pb2 Pa2 Kg1 Rf1 Bc1 Nb1 Ra1 ']]]


#Moves: 42, #Winning: 38, #Losing: 4
[0.6, Move.from_uci('h8a8'), [[27.86680793762207, <Outcome.WHITE_WON: 1>, 'https://lichess.org/xNnQn1jW#63', 'ra8 kd7 bc7 Qa7 ph6 qc6 Pb6 pg5 Pf5 pc5 Pg3 Pf2 Bd2 Pc2 Pb2 Re1 Kc1 '], [26.249279022216797, <Outcome.BLACK_WON: -1>, 'https://lichess.org/7HsJdlYZ#57', 'rf8 kd8 ra8 qg7 bc7 pa7 Qc6 pb6 ph4 Pf4 Pd4 Ph3 Pc3 Pg2 Pb2 Pa2 Kg1 Re1 Bc1 Ra1 '], [25.602067947387695, <Outcome.BLACK_WON: -1>, 'https://lichess.org/UD328rgY#47', 'rh8 ra8 kg7 pf7 be7 pb7 pe6 Pb6 pf5 Pe5 pd5 ph4 Pf4 ne4 Nd4 qc4 Ph3 Qf3 Pc3 Pg2 Kg1 Be1 Rb1 Ra1 '], [25.58765983581543, <Outcome.BLACK_WON: -1>, 'https://lichess.org/ctOq4EXm#37', 'rh8 rb8 pg7 pf7 kd7 bc7 Qb7 ph6 qf6 pe6 nc6 nh5 pd5 Nc5 Pd4 Ph3 Pf3 Be3 Pc3 Pf2 Pb2 Pa2 Rg1 Rd1 Kb1 '], [25.542678833007812, <Outcome.WHITE_WON: 1>, 'https://lichess.org/MPVn4JO7#77', 'pg7 pf7 kd7 pb7 ph6 pe6 Pb6 Pg4 Pf4 Nd4 Ph3 Kf2 bc2 ']]]


#Moves: 39, #Winning: 8, #Losing: 31
[0.6, Move.from_uci('b4b7'), [[30.649038314819336, <Outcome.BLACK_WON: -1>, 'https://lichess.org/KOCGKsPa#70', 'kg8 pg7 pf7 ph6 pc6 Pe5 pa5 Qf4 pb4 Pa4 Ph3 Nf3 Kh2 Pg2 qf2 Pc2 Pb2 rd1 '], [29.485424041748047, <Outcome.BLACK_WON: -1>, 'https://lichess.org/i9SYcuF8#45', 'kg8 re8 ra8 ph7 bg7 pf7 Rc7 pb7 pa7 pg6 pd5 Qf4 Ph3 Pa3 Kh2 Pg2 Pf2 Pb2 Ba2 qf1 '], [28.327255249023438, <Outcome.WHITE_WON: 1>, 'https://lichess.org/Isfpkdg8#71', 'kf8 ra8 pf7 Rb7 pg6 Qf6 pe6 pc6 ph5 Pc5 pa5 Pa4 Ph3 Kh2 Pg2 Pf2 rd1 '], [28.173669815063477, <Outcome.WHITE_WON: 1>, 'https://lichess.org/N9G4SwC0#105', 'kg8 ph7 pf7 pg6 pe6 Pe5 Qf4 Pd4 Ph3 Nf3 Kh2 Pg2 qf1 '], [28.153636932373047, <Outcome.WHITE_WON: 1>, 'https://lichess.org/omrfbS4D#68', 'kh8 ph7 bg7 pg6 rf5 Qg4 Ph3 Nf3 Pg2 qe2 Pc2 Pb2 Pa2 Kh1 Rd1 ']]]


#Moves: 26, #Winning: 21, #Losing: 5
[1.0, Move.from_uci('h4h8'), [[38.69956588745117, <Outcome.WHITE_WON: 1>, 'https://lichess.org/1lfuLWwn#55', 'Qh8 kf8 pg7 pf7 ne7 qd7 bc7 pe6 pa6 Pe5 Bc5 pb5 Pf4 pc4 Pg3 Pc3 Pa3 Ph2 Bc2 Pb2 Kg1 '], [37.306705474853516, <Outcome.WHITE_WON: 1>, 'https://lichess.org/zmRgw186#49', 'Qh8 kf8 ne8 bc8 bb8 pg7 re7 qd7 rc7 pa7 pe6 Ng5 Pe5 pd5 pb5 Ng4 Pd4 pc4 Pg3 Pc3 Ph2 Bg2 Pb2 Pa2 Kg1 Bc1 Ra1 '], [33.561283111572266, <Outcome.WHITE_WON: 1>, 'https://lichess.org/Yktimka1#60', 'bh8 kf8 re8 nc8 Qh7 pf7 bd7 pg6 qf6 pe6 Ng5 Pf5 Pe5 pd5 pb5 Pd4 pc4 ra4 Pc3 Ph2 Kg2 Pf2 Ne2 Pb2 Re1 Rd1 Bb1 '], [32.86873245239258, <Outcome.WHITE_WON: 1>, 'https://lichess.org/Su6JzJoo#45', 'kg8 rf8 ra8 Qh7 pg7 qd7 pc7 pe6 Ng5 pd5 pb5 pa5 Pd4 Be3 Ph2 Pg2 Pf2 Pa2 Kf1 '], [32.821510314941406, <Outcome.WHITE_WON: 1>, 'https://lichess.org/laz390K3#55', 'Qh8 kf8 rb8 pg7 pf7 bd7 qc7 pg6 pe6 Ng5 Pe5 pd5 pc4 Pg3 Pc3 rb3 pa3 Ph2 Pf2 Re2 Pb2 Kg1 Rb1 ']]]


#Moves: 2, #Winning: 0, #Losing: 2
[0.2, Move.from_uci('g8h7'), [[44.95507049560547, <Outcome.WHITE_WON: 1>, 'https://lichess.org/pY2M2xI2#26', 'rf8 qd8 bc8 ra8 kh7 pg7 pf7 pb7 pa7 bf6 pe6 pc6 Ph4 Pd4 Pc4 Nf3 Pg2 Pf2 Pb2 Pa2 Rh1 Ke1 Qd1 Ra1 '], [44.7315559387207, <Outcome.WHITE_WON: 1>, 'https://lichess.org/ZzmSJzRY#24', 'kh8 rf8 qd8 bc8 ra8 Bh7 pg7 pf7 pc7 pb7 pa7 bf6 pe6 Ph4 Pd4 Nf3 Pc3 Pg2 Pf2 Pb2 Pa2 Rh1 Ke1 Qd1 Ra1 '], [42.99263381958008, <Outcome.WHITE_WON: 1>, 'https://lichess.org/F0IfjvhK#16', 'rf8 qd8 bc8 nb8 ra8 kh7 pg7 pf7 pc7 pa7 bf6 pe6 pb6 pd5 Ph4 Pd4 Nf3 Pe3 Pg2 Pf2 Pc2 Pb2 Pa2 Rh1 Ke1 Qd1 Nb1 Ra1 '], [41.71757507324219, <Outcome.WHITE_WON: 1>, 'https://lichess.org/vZSZ10DF#20', 'rf8 qd8 bc8 nb8 ra8 kh7 pg7 pf7 pc7 pb7 pa7 bf6 pe6 Ph4 Pd4 Nf3 Pg2 Pf2 Pb2 Pa2 Rh1 Ke1 Qd1 Nb1 Ra1 '], [41.600257873535156, <Outcome.BLACK_WON: -1>, 'https://lichess.org/DHJKcYAB#22', 'rf8 qd8 bc8 ra8 kh7 pg7 pf7 pb7 pa7 bf6 pe6 nc6 Ph4 Pd4 pc4 Nf3 Nc3 Pg2 Pf2 Pb2 Pa2 Rh1 Ke1 Qd1 Ra1 ']]]


In [20]:
print(len(res))
print(len(pred_correct))
print(len(pred_wrong))

116
70
46


In [25]:
directory = NIOFSDirectory(Paths.get("/Users/tobiaswilfert/Documents/University/IR/chess-db/games.index"))
searcher = IndexSearcher(DirectoryReader.open(directory))
searcher.setSimilarity(BM25Similarity())
analyzer = WhitespaceAnalyzer()

try:
    for i in range(16,100):
        puzzle = get_puzzle_board(i)
        solution = chess.Move.from_uci(get_puzzle_solution(i))
        display(HTML(chess.svg.board(board=puzzle, lastmove=solution, size=200)))
        temp = evaluate_position(puzzle.turn, puzzle, False, top=5, bound=50)
        print(f"#Moves: {puzzle.legal_moves.count()}, #Winning: {len([x for x in temp if x[0] > 0.5])}, #Losing: {len([x for x in temp if x[0] <= 0.5])}")
        solution_score = [x for x in temp if x[1] == solution][0]
        print(solution_score)
        if solution_score[0] > 0.5:
            pred_correct.append((i,solution_score))
            res.append(1)
        else:
            pred_wrong.append((i,solution_score))
            res.append(0)
except:
    del searcher

#Moves: 8, #Winning: 3, #Losing: 5
[0.6, Move.from_uci('g3g4'), [[25.625059127807617, <Outcome.WHITE_WON: 1>, 'https://lichess.org/Qq9yZint#89', 'ph6 Re6 pb6 pg5 pc5 pa5 Pg4 kf4 Pc4 Pa4 Kc3 Pb3 '], [25.560802459716797, <Outcome.WHITE_WON: 1>, 'https://lichess.org/oP30eB0X#91', 'pg5 pa5 Pg4 kf4 Kd4 Pc4 Pa4 Pb3 '], [25.531789779663086, <Outcome.WHITE_WON: 1>, 'https://lichess.org/a4u1tWZN#84', 'pd6 pg5 Pd5 pa5 Pg4 kf4 Pc4 Pa4 Kd3 '], [24.47796058654785, <Outcome.BLACK_WON: -1>, 'https://lichess.org/B6CgRsra#91', 'Bd6 pc6 pg5 kf5 Pc5 Pg4 pe4 Kd4 pf2 '], [24.36012077331543, <Outcome.BLACK_WON: -1>, 'https://lichess.org/uWKKRvLA#85', 'ph6 Ph5 pg5 pc5 Pg4 kf4 pd4 Pc4 Kd3 Pb3 ']]]


#Moves: 42, #Winning: 12, #Losing: 30
[0.2, Move.from_uci('d5f6'), [[52.74748229980469, <Outcome.DRAW: 0>, 'https://lichess.org/9vjdh2eL#22', 'rh8 bf8 rd8 kc8 ph7 pg7 pf7 pc7 pb7 pa7 nf6 be6 qd6 Qe4 Bc4 Pe3 Ph2 Pg2 Pf2 Pc2 Pb2 Pa2 Kg1 Rf1 Bc1 Nb1 Ra1 '], [50.89165496826172, <Outcome.BLACK_WON: -1>, 'https://lichess.org/KGBxHUWr#25', 'rh8 rd8 kc8 pg7 pf7 be7 pc7 pb7 pa7 pg6 pe6 qd6 nc6 Ne5 Pd4 Ph3 Pc3 Pg2 Pf2 Qe2 Pc2 Pa2 Kg1 Rf1 Bc1 Ra1 '], [49.3574104309082, <Outcome.WHITE_WON: 1>, 'https://lichess.org/1C7kvENA#31', 're8 rd8 kc8 pf7 pc7 pb7 ph6 pe6 qd6 nc6 pa6 pg5 Ne5 Qe4 Pd4 Ph3 Pc3 Pg2 Pf2 Pb2 Pa2 Kg1 Re1 Ra1 '], [48.93642807006836, <Outcome.WHITE_WON: 1>, 'https://lichess.org/WmrUJqQV#41', 'rh8 rd8 kb8 ph7 Nf7 be7 pc7 pb7 pa7 bg6 qd6 nc6 Ne5 nd5 Pg4 Bh3 Pd3 Ph2 Pc2 Pb2 Pa2 Kg1 Rf1 Qe1 Bc1 Ra1 '], [48.59632110595703, <Outcome.WHITE_WON: 1>, 'https://lichess.org/HjyY5rsr#18', 'rh8 rd8 kc8 ph7 pg7 pf7 pc7 pb7 pa7 nf6 be6 qd6 nc6 Ng5 bc5 pd4 Bc4 Ph2 Pg2 Pf2 Pc2 Pb2 Pa2 Kg1 Re1 Qd1 Bc1 N

#Moves: 34, #Winning: 15, #Losing: 19
[0.6, Move.from_uci('h5h4'), [[26.96371841430664, <Outcome.BLACK_WON: -1>, 'https://lichess.org/Qz30JfPO#90', 'ke6 pb6 pg5 ne5 pc5 Pb5 ph4 Pe4 Pc4 Kg3 Be2 '], [26.078794479370117, <Outcome.BLACK_WON: -1>, 'https://lichess.org/NZy4Oh2K#86', 'kd6 pc6 pg5 bf5 Nc5 ph4 Pf4 Pc4 Pb4 Kg3 Pb3 '], [26.041807174682617, <Outcome.WHITE_WON: 1>, 'https://lichess.org/NbRmhBJv#78', 're8 pa7 kg6 pc6 pb6 pg5 ph4 Pg4 Pf4 Pc4 Kg3 Pb3 Pa2 '], [25.847082138061523, <Outcome.WHITE_WON: 1>, 'https://lichess.org/zsv3FfsD#68', 'kc8 pf7 pb6 pg5 qf5 Pe5 pc5 Pb5 pa5 ph4 Pf4 be4 Pa4 Ph3 Qe3 Kh2 Pg2 Nd1 '], [25.76145362854004, <Outcome.BLACK_WON: -1>, 'https://lichess.org/euCSeyy6#84', 'pb6 pg5 pc5 ph4 Pf4 Pe4 kd4 Pc4 Pa4 Kg3 ']]]


#Moves: 42, #Winning: 23, #Losing: 19
[0.8, Move.from_uci('c3c2'), [[63.48506546020508, <Outcome.BLACK_WON: -1>, 'https://lichess.org/8FXryRkd#102', 'kg7 pg6 pe6 bc6 pa6 qe5 pb5 ph4 Pe4 Ph3 Qd3 pb3 Pg2 pc2 Kh1 Bb1 '], [61.63765335083008, <Outcome.BLACK_WON: -1>, 'https://lichess.org/CwfedOPe#70', 'kh8 be8 rd8 ph7 bg7 qb7 Qf5 pa5 Pa4 Ph3 pd3 Pb3 Ba3 Pg2 pc2 Kg1 Re1 Bb1 '], [61.32272720336914, <Outcome.WHITE_WON: 1>, 'https://lichess.org/eJMxHjFw#80', 'kg8 re8 pf7 ph6 pg5 Pf5 qc4 nb4 pa4 Pg3 Ph2 Kg2 Nf2 pc2 Bb1 Ra1 '], [58.41401290893555, <Outcome.BLACK_WON: -1>, 'https://lichess.org/ns3OgGWu#90', 'kh8 ph7 pg6 bc5 Nb5 rf2 pc2 Kh1 Bb1 '], [58.29001998901367, <Outcome.BLACK_WON: -1>, 'https://lichess.org/zj7lx1XY#95', 'bg7 kg5 pe5 nc5 Pg4 bf3 pa3 rg2 qd2 pc2 rb2 Kf1 Bb1 ']]]


#Moves: 46, #Winning: 15, #Losing: 31
[0.4, Move.from_uci('e2f2'), [[38.5078010559082, <Outcome.BLACK_WON: -1>, 'https://lichess.org/EWo4Y58f#43', 'kg8 rd8 ph7 pg7 pf7 pa7 pf6 pb6 bc5 Qb5 qf4 Pa3 Ph2 Pg2 rf2 Pb2 Kh1 Rf1 Rc1 '], [33.61885452270508, <Outcome.BLACK_WON: -1>, 'https://lichess.org/WvicIf0Z#62', 'kh7 pg7 pf7 ph5 Pf5 Qd5 Pc5 pa5 qf4 bd4 Ph3 Pa3 Pg2 rf2 Kg1 Rf1 Nb1 '], [33.35773849487305, <Outcome.WHITE_WON: 1>, 'https://lichess.org/dtJghc2K#54', 'rh8 kg7 pb7 pg6 pf6 pe6 Qd6 pa6 pd5 qh4 Pg4 Pf3 Pg2 rf2 Pb2 Pa2 Kg1 Rf1 '], [32.94078826904297, <Outcome.WHITE_WON: 1>, 'https://lichess.org/x1UO9tbC#38', 'kh8 ph7 pg7 pc7 pb7 pa7 bb6 Qd5 qh4 Pc3 Ph2 Pg2 rf2 Pb2 Pa2 Kh1 Rf1 Ra1 '], [31.998756408691406, <Outcome.WHITE_WON: 1>, 'https://lichess.org/4lgGHT2v#56', 'kh7 pf7 pb7 pa7 pg6 pd6 ph5 Qd5 pc5 qf4 Ph3 Bc3 Pg2 rf2 Pb2 Pa2 Kh1 Rd1 ']]]


...

#Moves: 27, #Winning: 15, #Losing: 12
[0.8, Move.from_uci('b4c3'), [[35.98335647583008, <Outcome.BLACK_WON: -1>, 'https://lichess.org/gttVttX8#53', 'kh8 rg8 ra8 pg7 ph6 Qg6 pf6 pc6 pd5 pb5 Ph4 qc4 Pf3 Pb3 Ba3 Pc2 Pa2 Rf1 Rd1 Kb1 '], [34.466819763183594, <Outcome.BLACK_WON: -1>, 'https://lichess.org/LiKoWtWZ#24', 'rh8 ng8 bf8 kd8 ra8 pg7 pe7 nd7 pb7 pa7 Qg6 pf6 qe6 pc6 ph5 pd5 Ph4 Bf4 Nc3 Pg2 Pf2 Ne2 Pc2 Pb2 Pa2 Rh1 Ke1 Ra1 '], [32.637535095214844, <Outcome.WHITE_WON: 1>, 'https://lichess.org/KbzjKjJc#46', 'rh8 kd8 rc8 pg7 qe7 nd7 Qg6 pf6 pe6 Ph5 pd5 pb5 pa5 Bf4 Pd4 nc4 bb4 Ng3 Pf3 Pb3 Ne2 Pc2 Pa2 Rh1 Rd1 Kb1 '], [32.41838455200195, <Outcome.BLACK_WON: -1>, 'https://lichess.org/clNH7WS3#69', 'kh7 re7 pb7 Ph6 pe6 bd6 pa6 Qh5 pf5 pd5 rg4 Pf4 Pd4 qc4 Rh3 pg3 Pb3 Rg2 Ne2 Pc2 Pa2 Kb1 '], [30.550527572631836, <Outcome.BLACK_WON: -1>, 'https://lichess.org/E1dsDpA9#50', 'bf8 kc8 Qh7 Rf7 nd7 ra7 pf6 pe6 pc6 pd5 Pd4 qb4 pa4 Bg3 Pf3 Pe3 Bd3 Pg2 Kf2 Pc2 ']]]


#Moves: 33, #Winning: 13, #Losing: 20
[0.2, Move.from_uci('h6g8'), [[42.15470886230469, <Outcome.WHITE_WON: 1>, 'https://lichess.org/bokWgV6G#57', 'kh8 rf8 rc8 qg7 bd7 pb7 Qg6 nf6 pd6 pa6 Pd5 Pg4 Ph3 Rf3 Bd3 Nc3 Pa3 Kg2 Pb2 Rf1 '], [40.86103439331055, <Outcome.DRAW: 0>, 'https://lichess.org/hKukd2NC#41', 'kg8 rf8 ra8 ph7 pg7 pf7 bd7 pc7 pb7 qg6 nf6 pd6 pe5 Pd5 pa5 Pg4 Pe4 Pc4 Ph3 Qg3 Rf3 Pe3 Bd3 Nc3 Pa3 Kh2 Pb2 Rf1 '], [40.47439193725586, <Outcome.BLACK_WON: -1>, 'https://lichess.org/TUCC05N4#51', 'bc8 ph7 kg7 pf7 qe7 nd7 pg6 nf6 rb6 Qg5 pe5 Pd5 pc5 ra5 Pe4 Pc4 pa4 Ph3 Ng3 Bd3 Pc3 Ba3 Kh2 Pg2 Rf2 Rf1 '], [39.195648193359375, <Outcome.BLACK_WON: -1>, 'https://lichess.org/U309yQBm#65', 'rf8 nh7 kg7 pf7 bd7 ra7 ph6 qd6 pb6 pa6 pg5 pe5 Pd5 pc5 Pg4 Nf4 Pe4 Pc4 Pa4 Ph3 Rf3 Nc3 Qg2 Bc2 Pb2 Kh1 Rf1 '], [38.66701126098633, <Outcome.BLACK_WON: -1>, 'https://lichess.org/g2zjXgvK#70', 'kh8 rf8 nh7 pg7 pf7 Ne7 pg6 nf6 qe6 Pd6 pa6 pb5 Qh4 Pg4 Ph3 Rd3 Pa3 Kh2 Pf2 Ba2 ']]]


#Moves: 50, #Winning: 21, #Losing: 29
[0.4, Move.from_uci('d1h5'), [[36.436744689941406, <Outcome.BLACK_WON: -1>, 'https://lichess.org/stvvKynj#28', 'kg8 rf8 qd8 rb8 ph7 pg7 pf7 be7 nd7 pa7 nf6 pe6 Bc6 pb6 Pd4 Pg3 pb3 Ph2 Pf2 Nd2 Bb2 Pa2 Kg1 Rf1 Qd1 Ra1 '], [36.247344970703125, <Outcome.BLACK_WON: -1>, 'https://lichess.org/DzrHEF1Q#50', 'kg8 rf8 qd8 rb8 pg7 pf7 nd7 ph6 pe6 nf5 Pe5 Qg4 Pe4 Pd4 pc4 Nf3 pb3 Ph2 Pg2 Pa2 Kg1 Rf1 Bc1 Ra1 '], [35.54111862182617, <Outcome.BLACK_WON: -1>, 'https://lichess.org/0Rm1D0IX#36', 'kg8 rf8 qd8 ra8 ph7 pg7 pf7 be7 nd7 pe6 pa6 Pg5 pe5 pb5 Ph4 Ng3 Qf3 pb3 Pf2 Pd2 Pc2 Bb2 Pa2 Rh1 Re1 Kc1 '], [35.055259704589844, <Outcome.WHITE_WON: 1>, 'https://lichess.org/odJaVPfV#27', 'kg8 rf8 qd8 rb8 ph7 pg7 pf7 be7 nd7 pc7 pe6 pa6 Qh5 Pe5 pb5 Be4 Pd4 Be3 Pa3 Ph2 Pg2 Pf2 Pc2 Pb2 Kg1 Rf1 Ra1 '], [34.18125534057617, <Outcome.WHITE_WON: 1>, 'https://lichess.org/dxn5UOX6#33', 'kg8 rf8 qd8 rb8 ph7 pg7 pf7 be7 nd7 pe6 Pe5 pd5 pa5 Pf4 Bd4 Nc3 Pa3 Ph2 Pg2 Qe2 Pb2 Kg1 Rf1 Rb1 ']

#Moves: 33, #Winning: 14, #Losing: 19
[0.4, Move.from_uci('f3d1'), [[42.1831169128418, <Outcome.WHITE_WON: 1>, 'https://lichess.org/GErtRTXy#61', 'kg8 re8 ra8 ph7 bg7 pg6 pf5 Nb5 pa5 pe4 Pc4 pb4 Ph3 Pg3 Pb3 Pf2 Re2 Bb2 Pa2 Ke1 '], [40.96400451660156, <Outcome.BLACK_WON: -1>, 'https://lichess.org/rAGHTYbK#54', 'kg8 rf8 ra8 ph7 bf7 qc7 pb7 pa7 pg6 pc6 pf5 pe4 Pc4 Pe3 Pb3 Pg2 Rf2 Bb2 Pa2 Kg1 Nf1 Bd1 Ra1 '], [39.92688751220703, <Outcome.DRAW: 0>, 'https://lichess.org/CMNWXuM7#30', 'kg8 rf8 rd8 ph7 bg7 nc7 pb7 pa7 pg6 be6 pc6 pf5 pe4 Pc4 Pg3 Pe3 Pb3 Ph2 Pf2 Ne2 Bc2 Bb2 Pa2 Kg1 Rf1 Ra1 '], [39.90825271606445, <Outcome.BLACK_WON: -1>, 'https://lichess.org/wspbgljs#63', 'kg8 rd8 pc7 pg6 pb6 ph5 pf5 pc5 pa5 Pf4 pe4 Pc4 Pg3 Be3 bd3 Pb3 Ph2 Kg2 Pa2 Re1 Bd1 '], [39.39626693725586, <Outcome.WHITE_WON: 1>, 'https://lichess.org/SIuWkCKq#52', 'kh8 rf8 rc8 nb8 ph7 pg7 bf6 pe6 bc6 pa6 pf5 pb5 pe4 Pb4 Pg3 Bb3 Pa3 Pg2 Pf2 Bb2 Kg1 Nf1 Rd1 Rc1 ']]]


#Moves: 37, #Winning: 9, #Losing: 28
[0.2, Move.from_uci('c6a8'), [[20.842065811157227, <Outcome.BLACK_WON: -1>, 'https://lichess.org/PdVmFidh#42', 'kh8 rf8 Bh7 pg7 pb7 pd5 Pc5 pa5 qh4 bh3 Nc3 Pa3 Qc2 Pb2 Kg1 Ra1 '], [20.827211380004883, <Outcome.BLACK_WON: -1>, 'https://lichess.org/MOf8LAtt#54', 'kg8 rf8 ra8 pg7 pb7 pa7 pc6 qh5 pd5 Pc5 Bd4 bh3 pf3 Pc3 Pf2 Qd2 Pb2 Pa2 Kg1 Re1 Ra1 '], [20.8105411529541, <Outcome.WHITE_WON: 1>, 'https://lichess.org/nbUcSSnT#41', 'kh8 rf8 ra8 ph7 Bg7 pc6 pc5 pa5 qh4 pf4 Pc4 bh3 Ng3 Pb3 Pa3 Ph2 Pf2 Qc2 Kg1 Rd1 Ra1 '], [20.762920379638672, <Outcome.BLACK_WON: -1>, 'https://lichess.org/6OAns1Yp#64', 'kh8 rf8 rb8 qh7 pe7 pd6 be5 Bd5 pc5 pf4 Pc4 Qa4 bh3 Pc3 Ph2 Rf2 Pe2 Pa2 Kh1 Be1 Ra1 '], [20.751916885375977, <Outcome.BLACK_WON: -1>, 'https://lichess.org/YAUn0Ons#50', 'kg8 ra8 ph7 pg7 re7 pc7 pb7 pa7 qh5 pd5 Pc5 bh3 pf3 Pb3 Ph2 Pf2 Qd2 Pa2 Kh1 Rg1 Rd1 ']]]


In [26]:
res = res[-100:]
pred_correct = pred_correct[-100:]
pred_wrong = pred_wrong[-100:]

In [32]:
print(len(res))
print(sum(res))
print(100-sum(res))

100
53
47


In [27]:
print(res)

[0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 0, 1, 0, 1, 1, 0, 1, 1, 0, 1, 0, 1, 0, 1, 0, 0, 0, 0, 1, 1, 0, 1, 1, 0, 1, 0, 1, 1, 0, 0, 1, 0, 1, 0, 1, 1, 0, 1, 1, 1, 1, 1, 0, 0, 0, 1, 1, 0, 0, 0, 1, 1, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 1, 1, 1, 0, 1, 0, 1, 0, 0, 1, 1, 0, 1, 1, 0, 0, 1, 0, 1, 0, 0, 0, 0]


In [28]:
print(pred_correct)

[(13, [0.8, Move.from_uci('d3e3'), [[30.201921463012695, <Outcome.BLACK_WON: -1>, 'https://lichess.org/9BYjEKBo#69', 'kg8 re8 pg7 re7 ph6 pf6 pd6 pc6 Pa5 Ph4 qg4 Pe4 pb4 Pg3 Qd3 Kh2 Pg2 Re2 Re1 '], [29.99567222595215, <Outcome.BLACK_WON: -1>, 'https://lichess.org/a2f8x5GB#51', 'kg8 rf8 ph7 pg7 pf7 Qb7 rh6 pa6 Ph4 qg4 Pg3 Pe3 Pc3 Pa3 Kg2 Pb2 Rf1 Rd1 '], [29.8835391998291, <Outcome.BLACK_WON: -1>, 'https://lichess.org/Y21zPSxc#72', 'kg8 re8 pg7 pf7 pa7 pb6 pc5 Qb5 Ph4 qg4 Pf4 Pg3 re3 Pa3 Kg2 Rf2 Pb2 '], [29.67519187927246, <Outcome.BLACK_WON: -1>, 'https://lichess.org/YAXngmzb#101', 'kg8 pg7 pb7 ph6 pa6 Pa5 Ph4 qg4 Pg3 rf3 pd3 Pb3 Kh2 Qg2 Rf2 '], [29.450305938720703, <Outcome.WHITE_WON: 1>, 'https://lichess.org/pJ7b6rGy#61', 'kg8 rf8 ph7 pg7 pf7 pa7 Ph4 qg4 Pg3 Pb3 Kg2 Rf2 Pa2 Re1 ']]]), (14, [0.6, Move.from_uci('e3e7'), [[37.57768249511719, <Outcome.BLACK_WON: -1>, 'https://lichess.org/9cptfFMj#56', 'rf8 kg7 nf7 Qe7 pa7 ph6 pb6 pg5 qf5 Pf3 Pc3 Bb3 Pa3 Ph2 Pg2 Kg1 Re1 '], [34.51834106445

In [29]:
print(pred_wrong)

[(0, [0.4, Move.from_uci('f6e4'), [[27.7602596282959, <Outcome.BLACK_WON: -1>, 'https://lichess.org/rzhHnipM#16', 'rh8 ke8 bc8 ra8 ph7 pg7 pf7 qe7 pc7 pb7 bd6 pc6 pa6 ne4 Pd4 Nf3 Nc3 Ph2 Pg2 Pf2 Pc2 Pb2 Pa2 Rh1 Ke1 Qd1 Bc1 Ra1 '], [27.619691848754883, <Outcome.BLACK_WON: -1>, 'https://lichess.org/RQmn2HYT#44', 'rd8 ph7 Rg7 pf7 ke7 pc7 pb7 pf6 pe6 pa6 be5 Ph4 Pf3 Be3 Pc3 Pf2 Ke2 Pb2 Pa2 '], [27.54792594909668, <Outcome.WHITE_WON: 1>, 'https://lichess.org/RqBAyMol#38', 'rh8 ke8 rd8 ph7 bg7 pf7 pg6 pa6 pb5 Bf4 ne4 pc4 Ph3 Nc3 Pg2 Pf2 Pc2 Pb2 Pa2 Rh1 Ke1 Ra1 '], [27.506332397460938, <Outcome.WHITE_WON: 1>, 'https://lichess.org/IK6kHoYP#32', 'ke8 qd8 ra8 ph7 pf7 pc7 pb7 pa7 bd6 Qa5 ne4 nd4 pc4 Pf3 Pd3 Nc3 Ph2 rg2 Pc2 Pb2 Pa2 Rh1 Ke1 Bc1 Ra1 '], [27.376846313476562, <Outcome.WHITE_WON: 1>, 'https://lichess.org/JAew4ZIj#32', 'rh8 rd8 ph7 pg7 kd7 pc7 pb7 nf6 bd6 pc6 pa6 Pd3 Nc3 Ph2 Pg2 Pf2 Pc2 Pb2 Pa2 Kf1 Re1 Bc1 Ra1 ']]]), (3, [0.4, Move.from_uci('c5a7'), [[27.099559783935547, <Outcome.WHITE_

In [30]:
correct_similarity = [x[1][2][0][0] for x in pred_correct]
wrong_similarity = [x[1][2][0][0] for x in pred_wrong]
print(sum(correct_similarity)/len(correct_similarity))
print(sum(wrong_similarity)/len(wrong_similarity))

correct_similarity = [sum([y[0] for y in x[1][2]])/5 for x in pred_correct]
wrong_similarity = [sum([y[0] for y in x[1][2]])/5 for x in pred_wrong]
print(sum(correct_similarity)/len(correct_similarity))
print(sum(wrong_similarity)/len(wrong_similarity))

35.99299883842468
36.45120438565029
33.78421065330505
34.244672048761615


# Test custom Cosine Similarity

In [25]:
from org.apache.pylucene.search.similarities import PythonClassicSimilarity
from math import log, sqrt

# See for documentation: https://lucene.apache.org/core/9_7_0/core/org/apache/lucene/search/similarities/package-summary.html
# https://lucene.apache.org/core/9_7_0/core/org/apache/lucene/search/similarities/SimilarityBase.html#score(org.apache.lucene.search.similarities.BasicStats,double,double)

class CosineSimilarity(PythonClassicSimilarity):
    def score(self, stats, freq, docLen):
        # Calculate the cosine similarity
        tf = freq.getValue()
        idf = log((stats.getNumberOfDocuments() + 1) / (stats.getDocFreq() + 1))
        norm = 1 / sqrt(docLen)
        score = tf * idf * norm
        return score

    def toString(self):
        return "CosineSimilarity"


In [26]:
directory = NIOFSDirectory(Paths.get("/Users/tobiaswilfert/Documents/University/IR/chess-db/games.index"))
searcher = IndexSearcher(DirectoryReader.open(directory))
searcher.setSimilarity(CosineSimilarity())
analyzer = WhitespaceAnalyzer()

fen = "8/p1pk4/1p2pp2/8/3P1P2/2P1KR1r/PP6/8"
board = chess.Board(fen)
display(HTML(chess.svg.board(board=board, size=200)))
temp = evaluate_position("", board, False, top=5, bound=40)
temp

[[0.6,
  Move.from_uci('f3h3'),
  [[12.608745574951172,
    <Outcome.BLACK_WON: -1>,
    'https://lichess.org/FBwV0PhU#64',
    'rh8 kc8 pc7 pa7 nf6 pe6 pb6 Pf4 pe4 Pd4 Pb4 Rg3 Ke3 Pc3 Pa2 Ba1 '],
   [12.5062255859375,
    <Outcome.WHITE_WON: 1>,
    'https://lichess.org/haaBuyQu#87',
    'pc7 pa7 kd6 pb6 Ke4 Pd4 Pc4 Pb4 Pa4 '],
   [12.330931663513184,
    <Outcome.DRAW: 0>,
    'https://lichess.org/0bVSKY3f#67',
    'ne7 pc7 pa7 pf6 kd6 pb6 ph5 Ph4 Pf4 Ke4 Pd4 Pc4 Pb4 Ph3 Pa3 '],
   [12.204686164855957,
    <Outcome.BLACK_WON: -1>,
    'https://lichess.org/mjEXwN8H#71',
    'rf8 kd7 pc7 pb7 pa7 pe6 Pd4 Ke3 Pc3 Pb3 Pa3 Rh2 '],
   [11.935600280761719,
    <Outcome.BLACK_WON: -1>,
    'https://lichess.org/UHErUpag#75',
    'pc7 kd6 pb6 pa5 Ke4 Pd4 Pc3 Nd2 Pb2 Pa2 ']]],
 [0.6,
  Move.from_uci('f3g3'),
  [[16.399337768554688,
    <Outcome.WHITE_WON: 1>,
    'https://lichess.org/7XwWqkUC#79',
    'pa7 kd6 pb6 pf5 Pf4 rh3 Rg3 Kf3 Pc2 Pb2 Pa2 '],
   [14.329401969909668,
    <Outcome.BLACK_WON

In [32]:
for t in temp[0][2]:
    print(t)
    board = decode_piece_position(t[3])
    display(HTML(chess.svg.board(board=board, size=200)))

[12.608745574951172, <Outcome.BLACK_WON: -1>, 'https://lichess.org/FBwV0PhU#64', 'rh8 kc8 pc7 pa7 nf6 pe6 pb6 Pf4 pe4 Pd4 Pb4 Rg3 Ke3 Pc3 Pa2 Ba1 ']


[12.5062255859375, <Outcome.WHITE_WON: 1>, 'https://lichess.org/haaBuyQu#87', 'pc7 pa7 kd6 pb6 Ke4 Pd4 Pc4 Pb4 Pa4 ']


[12.330931663513184, <Outcome.DRAW: 0>, 'https://lichess.org/0bVSKY3f#67', 'ne7 pc7 pa7 pf6 kd6 pb6 ph5 Ph4 Pf4 Ke4 Pd4 Pc4 Pb4 Ph3 Pa3 ']


[12.204686164855957, <Outcome.BLACK_WON: -1>, 'https://lichess.org/mjEXwN8H#71', 'rf8 kd7 pc7 pb7 pa7 pe6 Pd4 Ke3 Pc3 Pb3 Pa3 Rh2 ']


[11.935600280761719, <Outcome.BLACK_WON: -1>, 'https://lichess.org/UHErUpag#75', 'pc7 kd6 pb6 pa5 Ke4 Pd4 Pc3 Nd2 Pb2 Pa2 ']


# Conclusion
Looks good, I guess but it very very slow. Need to optimize it.

In [35]:
#from lucene import SimilarityBase
from org.apache.lucene.search.similarities import SimilarityBase
from org.apache.pylucene.search.similarities import PythonSimilarity


class _TEST(PythonSimilarity):
    def __init__(self_):
        # super(_TEST, self_).__init__()
        pass
    
    def score(self, stats, freq, docLen):
        # Calculate the cosine similarity
        tf = freq.getValue()
        idf = log((stats.getNumberOfDocuments() + 1) / (stats.getDocFreq() + 1))
        norm = 1 / sqrt(docLen)
        _score = tf * idf * norm
        return _score

    def toString(self):
        return "CosineSimilarity"

_TEST()

<_TEST: <null>>

In [36]:
directory = NIOFSDirectory(Paths.get("/Users/tobiaswilfert/Documents/University/IR/chess-db/games.index"))
searcher = IndexSearcher(DirectoryReader.open(directory))
searcher.setSimilarity(_TEST())
analyzer = WhitespaceAnalyzer()

fen = "8/p1pk4/1p2pp2/8/3P1P2/2P1KR1r/PP6/8"
board = chess.Board(fen)
display(HTML(chess.svg.board(board=board, size=200)))
temp2 = score_lookup(board, 40)
temp2

JavaError: <super: <class 'JavaError'>, <JavaError object>>
    Java stacktrace:
java.lang.NullPointerException: Cannot invoke "org.apache.lucene.search.similarities.Similarity.scorer(float, org.apache.lucene.search.CollectionStatistics, org.apache.lucene.search.TermStatistics[])" because "this.similarity" is null
	at org.apache.lucene.search.TermQuery$TermWeight.<init>(TermQuery.java:75)
	at org.apache.lucene.search.TermQuery.createWeight(TermQuery.java:233)
	at org.apache.lucene.search.BoostQuery.createWeight(BoostQuery.java:123)
	at org.apache.lucene.search.IndexSearcher.createWeight(IndexSearcher.java:904)
	at org.apache.lucene.search.BooleanWeight.<init>(BooleanWeight.java:59)
	at org.apache.lucene.search.BooleanQuery.createWeight(BooleanQuery.java:245)
	at org.apache.lucene.search.IndexSearcher.createWeight(IndexSearcher.java:904)
	at org.apache.lucene.search.IndexSearcher.search(IndexSearcher.java:687)
	at org.apache.lucene.search.IndexSearcher.searchAfter(IndexSearcher.java:523

In [38]:
#from lucene import SimilarityBase
from org.apache.lucene.search.similarities import SimilarityBase
from org.apache.pylucene.search.similarities import PythonSimilarity


class _TEST(PythonSimilarity):
    # def __init__(self_):
    #     # super(_TEST, self_).__init__()
    #     pass
    
    def score(self, stats, freq, docLen):
        # Calculate the cosine similarity
        tf = freq.getValue()
        idf = log((stats.getNumberOfDocuments() + 1) / (stats.getDocFreq() + 1))
        norm = 1 / sqrt(docLen)
        _score = tf * idf * norm
        return _score

    def toString(self):
        return "CosineSimilarity"

directory = NIOFSDirectory(Paths.get("/Users/tobiaswilfert/Documents/University/IR/chess-db/games.index"))
searcher = IndexSearcher(DirectoryReader.open(directory))
searcher.setSimilarity(_TEST())
analyzer = WhitespaceAnalyzer()

fen = "8/p1pk4/1p2pp2/8/3P1P2/2P1KR1r/PP6/8"
board = chess.Board(fen)
display(HTML(chess.svg.board(board=board, size=200)))
temp2 = score_lookup(board, 1)
temp2

RecursionError: maximum recursion depth exceeded while calling a Python object

interesting

In [28]:
from org.apache.lucene.search.similarities import ClassicSimilarity

directory = NIOFSDirectory(Paths.get("/Users/tobiaswilfert/Documents/University/IR/chess-db/games.index"))
searcher = IndexSearcher(DirectoryReader.open(directory))
# Interesting read: https://lucene.apache.org/core/9_7_0/core/org/apache/lucene/search/similarities/TFIDFSimilarity.html
searcher.setSimilarity(ClassicSimilarity())
analyzer = WhitespaceAnalyzer()

fen = "8/p1pk4/1p2pp2/8/3P1P2/2P1KR1r/PP6/8"
board = chess.Board(fen)
display(HTML(chess.svg.board(board=board, size=200)))
temp2 = score_lookup(board, 40)
temp2

[['qgO0BriP.txt',
  '51',
  'https://lichess.org/qgO0BriP#51',
  17.457855224609375,
  'kc8 be7 pd7 pc7 bb7 pa7 pe6 pb6 na6 Pf4 Pd4 rh3 Rf3 Ke3 Pc3 Pb2 Pa2 Re1 ',
  "Headers(Event='Rated Blitz game', Site='https://lichess.org/qgO0BriP', Date='2023.09.01', Round='-', White='Letlotlo_Tiiso', Black='agtzr_Frye', Result='0-1', UTCDate='2023.09.01', UTCTime='00:21:34', WhiteElo='1853', BlackElo='1848', WhiteRatingDiff='-6', BlackRatingDiff='+6', ECO='C00', Opening='French Defense: Knight Variation', TimeControl='300+0', Termination='Normal')"],
 ['fUtaR0AS.txt',
  '98',
  'https://lichess.org/fUtaR0AS#98',
  15.931920051574707,
  'kf8 pa7 pe6 Pe5 pd5 Pf4 Pd4 rh3 Rf3 Ke3 Pc3 ',
  "Headers(Event='Rated Bullet tournament https://lichess.org/tournament/zK7gBbue', Site='https://lichess.org/fUtaR0AS', Date='2023.09.01', Round='-', White='BRF-2011', Black='sagargandhi25', Result='1-0', UTCDate='2023.09.01', UTCTime='01:23:47', WhiteElo='1945', BlackElo='1735', WhiteRatingDiff='+3', BlackRatingDiff

In [30]:
for t in temp2[:10]:
    print(t)
    board = decode_piece_position(t[4])
    display(HTML(chess.svg.board(board=board, size=200)))

['qgO0BriP.txt', '51', 'https://lichess.org/qgO0BriP#51', 17.457855224609375, 'kc8 be7 pd7 pc7 bb7 pa7 pe6 pb6 na6 Pf4 Pd4 rh3 Rf3 Ke3 Pc3 Pb2 Pa2 Re1 ', "Headers(Event='Rated Blitz game', Site='https://lichess.org/qgO0BriP', Date='2023.09.01', Round='-', White='Letlotlo_Tiiso', Black='agtzr_Frye', Result='0-1', UTCDate='2023.09.01', UTCTime='00:21:34', WhiteElo='1853', BlackElo='1848', WhiteRatingDiff='-6', BlackRatingDiff='+6', ECO='C00', Opening='French Defense: Knight Variation', TimeControl='300+0', Termination='Normal')"]


['fUtaR0AS.txt', '98', 'https://lichess.org/fUtaR0AS#98', 15.931920051574707, 'kf8 pa7 pe6 Pe5 pd5 Pf4 Pd4 rh3 Rf3 Ke3 Pc3 ', "Headers(Event='Rated Bullet tournament https://lichess.org/tournament/zK7gBbue', Site='https://lichess.org/fUtaR0AS', Date='2023.09.01', Round='-', White='BRF-2011', Black='sagargandhi25', Result='1-0', UTCDate='2023.09.01', UTCTime='01:23:47', WhiteElo='1945', BlackElo='1735', WhiteRatingDiff='+3', BlackRatingDiff='-3', ECO='A40', Opening='Horwitz Defense', TimeControl='30+0', Termination='Time forfeit')"]


['kwZqPqpu.txt', '71', 'https://lichess.org/kwZqPqpu#71', 14.844488143920898, 'pg7 ke7 qb7 pg6 pf6 pe6 pc5 Bb5 pa5 Qg4 Pf4 Pd4 Pa4 rh3 Rf3 Ke3 Pc3 rh1 Rc1 ', "Headers(Event='Rated Blitz game', Site='https://lichess.org/kwZqPqpu', Date='2023.09.01', Round='-', White='amiccal', Black='UnitedIndiaChess', Result='0-1', UTCDate='2023.09.01', UTCTime='03:19:15', WhiteElo='2102', BlackElo='2102', WhiteRatingDiff='-6', BlackRatingDiff='+8', ECO='A04', Opening='Zukertort Opening: Slav Invitation', TimeControl='180+0', Termination='Normal')"]


['j2BKDqJg.txt', '56', 'https://lichess.org/j2BKDqJg#56', 14.262146949768066, 'pg7 ke7 pb7 pa7 pe6 pc6 Pg5 Pe5 Pf4 Ne4 rh3 Rf3 Ke3 Pc3 Pb3 rh2 Pa2 Ra1 ', 'Headers(Event=\'Rated Bullet tournament https://lichess.org/tournament/xwRYxgtz\', Site=\'https://lichess.org/j2BKDqJg\', Date=\'2023.09.01\', Round=\'-\', White=\'Venom1507\', Black=\'Riomsaro\', Result=\'0-1\', UTCDate=\'2023.09.01\', UTCTime=\'03:02:23\', WhiteElo=\'1965\', BlackElo=\'1862\', WhiteRatingDiff=\'-7\', BlackRatingDiff=\'+7\', ECO=\'D02\', Opening="Queen\'s Pawn Game: Zukertort Variation", TimeControl=\'60+0\', Termination=\'Time forfeit\')']


['KBzKMiq7.txt', '137', 'https://lichess.org/KBzKMiq7#137', 13.86309814453125, 'kd6 re4 Pb4 rh3 Rf3 Pa3 Kf2 ', "Headers(Event='Rated Blitz game', Site='https://lichess.org/KBzKMiq7', Date='2023.09.01', Round='-', White='Ronaldws', Black='diane75', Result='0-1', UTCDate='2023.09.01', UTCTime='04:16:47', WhiteElo='1507', BlackElo='1542', WhiteRatingDiff='-6', BlackRatingDiff='+5', ECO='A45', Opening='Indian Defense', TimeControl='300+0', Termination='Time forfeit')"]


['HgvMehNo.txt', '136', 'https://lichess.org/HgvMehNo#136', 13.806314468383789, 'rh3 Rf3 kg2 Ke2 ', 'Headers(Event=\'Rated Blitz game\', Site=\'https://lichess.org/HgvMehNo\', Date=\'2023.09.01\', Round=\'-\', White=\'Rokkie15\', Black=\'Viktor_Bozhenko\', Result=\'1/2-1/2\', UTCDate=\'2023.09.01\', UTCTime=\'06:33:22\', WhiteElo=\'1761\', BlackElo=\'1787\', WhiteRatingDiff=\'+0\', BlackRatingDiff=\'-1\', ECO=\'D00\', Opening="Queen\'s Pawn Game", TimeControl=\'180+0\', Termination=\'Normal\')']


['Ha5xH7Hi.txt', '61', 'https://lichess.org/Ha5xH7Hi#61', 13.605306625366211, 'rg8 kc8 ph7 pc7 pa7 pc6 pf5 Pd4 rg3 Rf3 Ke3 Pc3 Pb2 Pa2 Rf1 ', "Headers(Event='Rated Bullet tournament https://lichess.org/tournament/6hVh7Hav', Site='https://lichess.org/Ha5xH7Hi', Date='2023.09.01', Round='-', White='MCklopediaofficial', Black='August-September2023', Result='1-0', UTCDate='2023.09.01', UTCTime='03:24:17', WhiteElo='2149', BlackElo='2103', WhiteRatingDiff='+43', BlackRatingDiff='-4', ECO='A00', Opening='Saragossa Opening', TimeControl='30+0', Termination='Time forfeit')"]


['7XwWqkUC.txt', '79', 'https://lichess.org/7XwWqkUC#79', 12.919571876525879, 'pa7 kd6 pb6 pf5 Pf4 rh3 Rg3 Kf3 Pc2 Pb2 Pa2 ', "Headers(Event='Rated Blitz game', Site='https://lichess.org/7XwWqkUC', Date='2023.09.01', Round='-', White='Your_3_0', Black='Ciriakov', Result='1-0', UTCDate='2023.09.01', UTCTime='02:28:49', WhiteElo='1979', BlackElo='1988', WhiteRatingDiff='+19', BlackRatingDiff='-6', ECO='A43', Opening='Benoni Defense: Old Benoni', TimeControl='180+0', Termination='Time forfeit')"]


['FBwV0PhU.txt', '64', 'https://lichess.org/FBwV0PhU#64', 12.819310188293457, 'rh8 kc8 pc7 pa7 nf6 pe6 pb6 Pf4 pe4 Pd4 Pb4 Rg3 Ke3 Pc3 Pa2 Ba1 ', "Headers(Event='Rated Blitz game', Site='https://lichess.org/FBwV0PhU', Date='2023.09.01', Round='-', White='LuizRic', Black='okkotv', Result='0-1', UTCDate='2023.09.01', UTCTime='01:58:57', WhiteElo='1785', BlackElo='1783', WhiteRatingDiff='-5', BlackRatingDiff='+6', ECO='C00', Opening='French Defense: Steinitz Attack', TimeControl='180+0', Termination='Time forfeit')"]


['uZWANlTZ.txt', '78', 'https://lichess.org/uZWANlTZ#78', 12.798888206481934, 'pc7 kf6 pb6 pa5 Pf4 Pe4 Pd4 Pa4 Rg3 Ke3 Pc3 rh1 ', 'Headers(Event=\'Rated Blitz game\', Site=\'https://lichess.org/uZWANlTZ\', Date=\'2023.09.01\', Round=\'-\', White=\'I8I9\', Black=\'tapoukitos\', Result=\'1/2-1/2\', UTCDate=\'2023.09.01\', UTCTime=\'01:07:59\', WhiteElo=\'1733\', BlackElo=\'1714\', WhiteRatingDiff=\'+0\', BlackRatingDiff=\'+0\', ECO=\'D07\', Opening="Queen\'s Gambit Declined: Chigorin Defense", TimeControl=\'180+2\', Termination=\'Normal\')']


In [41]:
from org.apache.pylucene.search.similarities import PythonClassicSimilarity
from math import log, sqrt

class JaccardSimilarity(PythonClassicSimilarity):
    def score(self, stats, freq, docLen):
        # Calculate the Jaccard similarity
        tf = freq.getValue()
        idf = log((stats.getNumberOfDocuments() + 1) / (stats.getDocFreq() + 1))  # Inverse document frequency
        jaccard = tf / (docLen + stats.getNumberOfDocuments() - tf)  # Jaccard similarity
        score = jaccard * idf
        return 0 # score

    def toString(self):
        return "JaccardSimilarity"



directory = NIOFSDirectory(Paths.get("/Users/tobiaswilfert/Documents/University/IR/chess-db/games.index"))
searcher = IndexSearcher(DirectoryReader.open(directory))
# Interesting read: https://lucene.apache.org/core/9_7_0/core/org/apache/lucene/search/similarities/TFIDFSimilarity.html
searcher.setSimilarity(JaccardSimilarity())
analyzer = WhitespaceAnalyzer()

fen = "8/p1pk4/1p2pp2/8/3P1P2/2P1KR1r/PP6/8"
board = chess.Board(fen)
display(HTML(chess.svg.board(board=board, size=200)))
temp2 = score_lookup(board, 40)
temp2

[['qgO0BriP.txt',
  '51',
  'https://lichess.org/qgO0BriP#51',
  17.457855224609375,
  'kc8 be7 pd7 pc7 bb7 pa7 pe6 pb6 na6 Pf4 Pd4 rh3 Rf3 Ke3 Pc3 Pb2 Pa2 Re1 ',
  "Headers(Event='Rated Blitz game', Site='https://lichess.org/qgO0BriP', Date='2023.09.01', Round='-', White='Letlotlo_Tiiso', Black='agtzr_Frye', Result='0-1', UTCDate='2023.09.01', UTCTime='00:21:34', WhiteElo='1853', BlackElo='1848', WhiteRatingDiff='-6', BlackRatingDiff='+6', ECO='C00', Opening='French Defense: Knight Variation', TimeControl='300+0', Termination='Normal')"],
 ['fUtaR0AS.txt',
  '98',
  'https://lichess.org/fUtaR0AS#98',
  15.931920051574707,
  'kf8 pa7 pe6 Pe5 pd5 Pf4 Pd4 rh3 Rf3 Ke3 Pc3 ',
  "Headers(Event='Rated Bullet tournament https://lichess.org/tournament/zK7gBbue', Site='https://lichess.org/fUtaR0AS', Date='2023.09.01', Round='-', White='BRF-2011', Black='sagargandhi25', Result='1-0', UTCDate='2023.09.01', UTCTime='01:23:47', WhiteElo='1945', BlackElo='1735', WhiteRatingDiff='+3', BlackRatingDiff